<a href="https://colab.research.google.com/github/CrowdSalat/ann-dynamical-systems/blob/master/predict_plane_state.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# predict plane state

Uses actions and a input state to predict the outputstate.

## imports

In [1]:
try:
  # %tensorflow_version only exists in Colab.
  %tensorflow_version 2.x
except Exception:
  pass

TensorFlow 2.x selected.


In [2]:
import pandas as pd
import numpy as np
import os
import sys
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error

from sklearn.model_selection import train_test_split


import tensorflow as tf
print(tf.__version__)
from tensorflow import keras

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import *

2.0.0-rc2


In [3]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 4003369569374339654
, name: "/device:XLA_CPU:0"
device_type: "XLA_CPU"
memory_limit: 17179869184
locality {
}
incarnation: 7590082853030248019
physical_device_desc: "device: XLA_CPU device"
, name: "/device:XLA_GPU:0"
device_type: "XLA_GPU"
memory_limit: 17179869184
locality {
}
incarnation: 1803129270458604030
physical_device_desc: "device: XLA_GPU device"
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 11330115994
locality {
  bus_id: 1
  links {
  }
}
incarnation: 16323019665114821302
physical_device_desc: "device: 0, name: Tesla K80, pci bus id: 0000:00:04.0, compute capability: 3.7"
]


## load files

In [0]:
file = 'dataset_all.csv'

In [5]:
from google.colab import drive
drive.mount('/content/drive')

root_dir = '/content/drive/My Drive/xplane_data' 
os.chdir(root_dir)
print ('working dir: ' + os.getcwd())

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive
working dir: /content/drive/My Drive/xplane_data


## actions & states
actions and states at time t are the input for the network.

the states at time t + 1 are the desired output of the network.


In [6]:
col_m_time      = '   missn,_time '
col_t_time      = '   _totl,_time '
col_yaw_v       = '   ____Q,rad/s '
col_heading_mag = '   hding,__mag '
col_yaw_deg     = '   _beta,__deg '
col_roll_deg    = '   _roll,__deg '
col_roll_v      = '   ____R,rad/s '
col_pitch_deg   = '   pitch,__deg '
col_pitch_v     = '   ____P,rad/s '
col_alt         = '   __alt,ftmsl '
col_vv          = '   __VVI,__fpm '
col_v           = '   Vtrue,_ktas '
col_rpm_prop    = '   rpm_1,_prop '
col_throttle     = '   thro1,_part '

cols_state = [ 
    col_yaw_v,
    col_yaw_deg,
    col_roll_deg,
    col_roll_v,
    col_pitch_deg,
    col_pitch_v,
    col_vv,
    col_alt,
    col_v,
    col_rpm_prop,
    col_throttle,
]

cols_time = [
    col_m_time,
    col_t_time,
]

col_elev_servo                  = '   _elev,servo '
col_ailrn_servo                  = '   ailrn,servo '
col_ruddr_servo                  = '   ruddr,servo '

cols_action = [
    col_elev_servo,
    col_ailrn_servo,
    col_ruddr_servo
]

# all input columns
cols_features = []
cols_features.extend(cols_state)
cols_features.extend(cols_action)

# orga column
col_dataset_index = 'dataset_index'
col_maneuver_index = 'maneuver_index'
col_maneuver_name = 'maneuver_name'
col_maneuver_datapoint_index = 'maneuver_datapoint_index'
col_maneuver_type = 'maneuver_type'


label_prefix = 't+1_'
cols_label = [label_prefix + col_state for col_state in cols_state]
print(cols_label)


['t+1_   ____Q,rad/s ', 't+1_   _beta,__deg ', 't+1_   _roll,__deg ', 't+1_   ____R,rad/s ', 't+1_   pitch,__deg ', 't+1_   ____P,rad/s ', 't+1_   __VVI,__fpm ', 't+1_   __alt,ftmsl ', 't+1_   Vtrue,_ktas ', 't+1_   rpm_1,_prop ', 't+1_   thro1,_part ']


In [1]:
def load_xplane_csv(csv_path, columns):
    return pd.read_csv(csv_path, delimiter=',', usecols = columns, 
                       float_precision='high')

df_features = load_xplane_csv(file, cols_features)

df_labels = load_xplane_csv(file, cols_label)

print(len(df_features))
print(len(df_labels))
assert(len(df_features) == len(df_labels))


NameError: ignored

drop nan rows in both features and in labels

In [8]:
df_nan = df_labels.isna().any(axis=1)

for i in range(0, len(df_nan)):
  if df_nan[i] == True:
    df_features.drop(index=i, inplace=True)

df_labels.dropna(inplace=True)

print(len(df_features))
print(len(df_labels))

380074
380074


In [0]:
def split_train_test(dataset):
  train_size = int(len(dataset) * 0.67)
  test_size = len(dataset) - train_size
  train, test = dataset[0:train_size,:], dataset[train_size:len(dataset),:]
  return train, test


In [0]:
features = df_features.values
labels = df_labels.values

#train_X, test_X = split_train_test(features)
#train_Y, test_Y = split_train_test(labels)
train_X, test_X, train_Y, test_Y  = train_test_split(features,labels, test_size=0.2, random_state=42)


In [11]:
print(train_X.shape)
print(train_Y.shape)
print(test_X.shape)
print(test_Y.shape)

(304059, 14)
(304059, 11)
(76015, 14)
(76015, 11)


In [12]:
features_nr = train_X.shape[1]
target_nr = train_Y.shape[1]


baseline_model = keras.Sequential()

baseline_model.add(Dense(1200,input_shape=(features_nr,), 
                         kernel_initializer='he_uniform'))
baseline_model.add(BatchNormalization())
baseline_model.add(ReLU())

baseline_model.add(Dense(600,input_shape=(features_nr,)))
baseline_model.add(BatchNormalization())
baseline_model.add(ReLU())

baseline_model.add(Dense(600,input_shape=(features_nr,)))
baseline_model.add(BatchNormalization())
baseline_model.add(ReLU())

baseline_model.add(Dense(target_nr ))

baseline_model.compile(optimizer='adam',
                       loss='mean_squared_error',
                       metrics=['accuracy', 'binary_crossentropy', 'mean_squared_error'])

baseline_model.summary()


Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 1200)              18000     
_________________________________________________________________
batch_normalization (BatchNo (None, 1200)              4800      
_________________________________________________________________
re_lu (ReLU)                 (None, 1200)              0         
_________________________________________________________________
dense_1 (Dense)              (None, 600)               720600    
_________________________________________________________________
batch_normalization_1 (Batch (None, 600)               2400      
_________________________________________________________________
re_lu_1 (ReLU)               (None, 600)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 600)               3

In [0]:
baseline_history = baseline_model.fit(train_X,
                                      train_Y,
                                      epochs=100,
                                      batch_size=64,
                                      validation_data=(test_X, test_Y),
                                      verbose=2)


Train on 304059 samples, validate on 76015 samples
Epoch 1/100
304059/304059 - 49s - loss: 239643.2601 - accuracy: 0.9321 - binary_crossentropy: -7.8118e+03 - mean_squared_error: 239642.8438 - val_loss: 2419.6636 - val_accuracy: 0.9976 - val_binary_crossentropy: -7.8610e+03 - val_mean_squared_error: 2419.6621
Epoch 2/100
304059/304059 - 47s - loss: 1400.8782 - accuracy: 0.9793 - binary_crossentropy: -7.8566e+03 - mean_squared_error: 1400.8789 - val_loss: 680.0648 - val_accuracy: 0.9965 - val_binary_crossentropy: -7.8632e+03 - val_mean_squared_error: 680.0651
Epoch 3/100
304059/304059 - 47s - loss: 820.5415 - accuracy: 0.9830 - binary_crossentropy: -7.8575e+03 - mean_squared_error: 820.5410 - val_loss: 487.1884 - val_accuracy: 0.9951 - val_binary_crossentropy: -7.8623e+03 - val_mean_squared_error: 487.1882
Epoch 4/100
304059/304059 - 47s - loss: 515.1695 - accuracy: 0.9880 - binary_crossentropy: -7.8582e+03 - mean_squared_error: 515.1696 - val_loss: 518.2013 - val_accuracy: 0.9962 - val

In [0]:
baseline_model.save_weights('./checkpoints/baseline_model')

In [13]:
features_nr = train_X.shape[1]
target_nr = train_Y.shape[1]


features_nr = train_X.shape[1]
target_nr = train_Y.shape[1]


bigger_model = keras.Sequential()

bigger_model.add(Dense(1200,input_shape=(features_nr,), 
                         kernel_initializer='he_uniform'))
bigger_model.add(BatchNormalization())
bigger_model.add(ReLU())

bigger_model.add(Dense(1000,input_shape=(features_nr,)))
bigger_model.add(BatchNormalization())
bigger_model.add(ReLU())

bigger_model.add(Dense(800,input_shape=(features_nr,)))
bigger_model.add(BatchNormalization())
bigger_model.add(ReLU())

bigger_model.add(Dense(target_nr ))

bigger_model.compile(optimizer='adam',
                       loss='mean_squared_error',
                       metrics=['accuracy', 'binary_crossentropy', 'mean_squared_error'])

bigger_model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_4 (Dense)              (None, 1200)              18000     
_________________________________________________________________
batch_normalization_3 (Batch (None, 1200)              4800      
_________________________________________________________________
re_lu_3 (ReLU)               (None, 1200)              0         
_________________________________________________________________
dense_5 (Dense)              (None, 1000)              1201000   
_________________________________________________________________
batch_normalization_4 (Batch (None, 1000)              4000      
_________________________________________________________________
re_lu_4 (ReLU)               (None, 1000)              0         
_________________________________________________________________
dense_6 (Dense)              (None, 800)              

In [0]:
checkpoint_path = './checkpoints/bigger'

cp_callback = tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_path,
                                                 save_weights_only=True,
                                                 verbose=1)

bigger_history = bigger_model.fit(train_X,
                                      train_Y,
                                      epochs=30,
                                      validation_data=(test_X, test_Y),
                                      verbose=2,
                                     callbacks=[cp_callback]
                                  )


Train on 304059 samples, validate on 76015 samples
Epoch 1/30

Epoch 00001: saving model to ./checkpoints/bigger
304059/304059 - 99s - loss: 106010.7560 - accuracy: 0.9574 - binary_crossentropy: -7.8283e+03 - mean_squared_error: 106010.8438 - val_loss: 554.7561 - val_accuracy: 0.9951 - val_binary_crossentropy: -7.8638e+03 - val_mean_squared_error: 554.7557
Epoch 2/30


In [0]:
bigger_model.save_weights('./checkpoints/bigger_model')
#bigger_model.load_weights('./checkpoints/bigger_model')

In [14]:
features_nr = train_X.shape[1]
target_nr = train_Y.shape[1]


smaller_model = keras.Sequential()

smaller_model.add(Dense(600,input_shape=(features_nr,), 
                         kernel_initializer='he_uniform'))
smaller_model.add(BatchNormalization())
smaller_model.add(ReLU())

smaller_model.add(Dense(400,input_shape=(features_nr,)))
smaller_model.add(BatchNormalization())
smaller_model.add(ReLU())

smaller_model.add(Dense(400,input_shape=(features_nr,)))
smaller_model.add(BatchNormalization())
smaller_model.add(ReLU())

smaller_model.add(Dense(target_nr ))

smaller_model.compile(optimizer='adam',
                       loss='mean_squared_error',
                       metrics=['accuracy', 'binary_crossentropy', 'mean_squared_error'])

smaller_model.summary()

Model: "sequential_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_8 (Dense)              (None, 600)               9000      
_________________________________________________________________
batch_normalization_6 (Batch (None, 600)               2400      
_________________________________________________________________
re_lu_6 (ReLU)               (None, 600)               0         
_________________________________________________________________
dense_9 (Dense)              (None, 400)               240400    
_________________________________________________________________
batch_normalization_7 (Batch (None, 400)               1600      
_________________________________________________________________
re_lu_7 (ReLU)               (None, 400)               0         
_________________________________________________________________
dense_10 (Dense)             (None, 400)              

In [0]:
checkpoint_path = './checkpoints/smaller'

cp_callback = tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_path,
                                                 save_weights_only=True,
                                                 verbose=1)
smaller_history = smaller_model.fit(train_X,
                                      train_Y,
                                      epochs=30,
                                      validation_data=(test_X, test_Y),
                                      verbose=2,
                                    callbacks=[cp_callback])


Train on 304059 samples, validate on 76015 samples
Epoch 1/30

Epoch 00001: saving model to ./checkpoints/smaller
304059/304059 - 84s - loss: 152836.5458 - accuracy: 0.9227 - binary_crossentropy: -7.8232e+03 - mean_squared_error: 152836.5938 - val_loss: 1699.3851 - val_accuracy: 0.9964 - val_binary_crossentropy: -7.8615e+03 - val_mean_squared_error: 1699.3856
Epoch 2/30

Epoch 00002: saving model to ./checkpoints/smaller
304059/304059 - 82s - loss: 1769.5663 - accuracy: 0.9795 - binary_crossentropy: -7.8559e+03 - mean_squared_error: 1769.5654 - val_loss: 1682.2987 - val_accuracy: 0.9946 - val_binary_crossentropy: -7.8643e+03 - val_mean_squared_error: 1682.2980
Epoch 3/30

Epoch 00003: saving model to ./checkpoints/smaller
304059/304059 - 82s - loss: 1044.1096 - accuracy: 0.9843 - binary_crossentropy: -7.8567e+03 - mean_squared_error: 1044.1106 - val_loss: 849.6961 - val_accuracy: 0.9976 - val_binary_crossentropy: -7.8635e+03 - val_mean_squared_error: 849.6965
Epoch 4/30

Epoch 00004: s

In [0]:
smaller_model.save_weights('./checkpoints/smaller_model')
#smaller_model.load_weights('./checkpoints/smaller_model')


In [0]:
def save_plots_before_show(diagramm_name):
  diagramm_folder = './diagramms'

  if not os.path.exists(diagramm_folder):
      os.makedirs(diagramm_folder)

  plt.savefig(diagramm_folder + '/' + diagramm_name +'.pdf')
  plt.savefig(diagramm_folder + '/' + diagramm_name +'.svg')
  plt.savefig(diagramm_folder + '/' + diagramm_name +'.png')

def plot_history(histories, key='mea
  plt.figure(figsize=(16,10))

  for name, history in histories:
    val = plt.plot(history.epoch, history.history['val_'+key],
                   '--', label=name.title()+' Val')
    plt.plot(history.epoch, history.history[key], color=val[0].get_color(),
             label=name.title()+' Train')

  plt.xlabel('Epochs')
  plt.ylabel(key.replace('_',' ').title())
  plt.legend()

  plt.xlim([0,max(history.epoch)])
  save_plots_before_show('baseline_model_history')
  plt.show()


plot_history([('baseline', baseline_history),
              ('smaller', smaller_history),
              ('bigger', bigger_history)])


SyntaxError: ignored

In [15]:
baseline_model.load_weights('./checkpoints/baseline_model')
smaller_model.load_weights('./checkpoints/smaller_model')
bigger_model.load_weights('./checkpoints/bigger_model')


In [17]:
baseline_mse = baseline_model.evaluate(test_X, test_Y)[0]
smaller_mse = smaller_model.evaluate(test_X, test_Y)[0]
bigger_mse = bigger_model.evaluate(test_X, test_Y)[0]

print(baseline_mse, smaller_mse, bigger_mse)

76015/1 [===============================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================